In [31]:
import pandas as pd
import numpy as np
from sklearn.linear_model import LinearRegression
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

### Load `hours_df` and filter out articles with 6 days of data

In [32]:
temp = pd.read_csv("hours_df.csv")
len(temp['link'].unique())

2534

In [33]:
hours_df = pd.read_csv("hours(may-sep).csv")
hours_df['normalised_interpolated_facebook_interactions'] = hours_df['interpolated_facebook_interactions']/1000

In [34]:
len(hours_df['link'].unique())

16234

In [35]:
articles_6_days = hours_df.loc[hours_df['day'] >= 6]['link'].unique()
hours_df = hours_df.loc[hours_df['link'].isin(articles_6_days)]

In [36]:
len(hours_df['link'].unique())

7291

In [37]:
hours_df.shape

(48547, 14)

# Logarithmic Function

In [38]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit
import plotly.graph_objects as go

def logarithm(x, a, b, c):
    return a * np.log(b * x) + c

In [39]:
# fitted plot of single article
first_df = hours_df.loc[hours_df['link']=='https://www.facebook.com/592308557475467_708534577981980']
x = first_df['day']
y = first_df['normalised_interpolated_facebook_interactions']
popt, pcov = curve_fit(logarithm, x, y, maxfev=100000)
fig = go.Figure(data=go.Scatter(x=x, y=y, mode='markers', name= 'data'))
fig.add_trace(go.Scatter(
    x=x, y=logarithm(x, *popt),
    name='Fitted Curve'
))
fig.show()

/opt/anaconda3/envs/news_matching/lib/python3.10/site-packages/pandas/core/arraylike.py:402: RuntimeWarning:

invalid value encountered in log



In [40]:
def get_log_coeff_df(hours_df):

    unique_articles = hours_df['link'].unique()
    log_coeff_df = pd.DataFrame()

    for article in unique_articles:

        temp = hours_df.loc[hours_df['link'] == article]
        x = temp['day']
        y = temp['normalised_interpolated_facebook_interactions']
        popt, pcov = curve_fit(logarithm, x, y)
        temp['log_coeff_a'] = [popt[0]]*temp.shape[0]
        temp['log_coeff_b'] = [popt[1]]*temp.shape[0]
        temp['log_coeff_c'] = [popt[2]]*temp.shape[0]
        temp['fitted_interpolated_facebook_interactions'] = temp['log_coeff_a'] * np.log(temp['log_coeff_b'] * temp['day']) + temp['log_coeff_c']
        
        log_coeff_df = log_coeff_df.append(temp)

    return log_coeff_df

In [ ]:
log_coeff_df = get_log_coeff_df(hours_df)

/opt/anaconda3/envs/news_matching/lib/python3.10/site-packages/pandas/core/arraylike.py:402: RuntimeWarning:

invalid value encountered in log

/var/folders/gv/wfw3k2b112s0fh1fzmtf7bsc0000gn/T/ipykernel_69775/3415713348.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/gv/wfw3k2b112s0fh1fzmtf7bsc0000gn/T/ipykernel_69775/3415713348.py:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/gv/wfw3k2b112s0fh1fzmtf7bsc0000gn/T/ipykernel_69775/3415713348.py:14: SettingWithCopyWarning:


A

In [ ]:
log_coeff_df

In [47]:
log_coeff_df.columns

Index(['Unnamed: 0.1', 'Unnamed: 0', 'day', 'headline', 'summary', 'link',
       'total_day_hours', 'hours_active', 'missed_hours',
       'facebook_interactions', 'delta_facebook_interactions',
       'interpolated_facebook_interactions', 'label',
       'normalised_interpolated_facebook_interactions', 'log_coeff_a',
       'log_coeff_b', 'log_coeff_c',
       'fitted_interpolated_facebook_interactions'],
      dtype='object')